# TODO:
### NOW:
- ~~enforce output format for gemini~~
- llama, gpt, ~~claude~~
   - send concurrent calls to all models at once
- ~~add evaluation if there is a golden set for individual model~~
- aggregation strategy and tie breaking
   - multiclass classification: ~~majority vote~~, baysian approach with GT
      - provide X labeles per class
- repeat the same thing for multi-label/ner

### LATER:
- secret management
- update readme
- add images



### nice things to do:
- add tqdm to asyncio calls
- proper logging

# Annotate

In [ ]:
from utils import Annotate
from datasets import load_set

seed =42

In [ ]:
gemini_prompt_template = """
<data_description>
{description}
</data_description>
-----------

<context>
{datapoint}
</context>
------------

<labels>
{labels}
</labels>
------------

INSTRUCTION:
- familirize yourself with the data using data_description
- read the context carefully. this is the data point you need to label.
- take your time and label the dadatapoint with the most appropriate option using the provided labels.
- return the result as a single label from the <labels>. Don't provide explanations
"""

In [ ]:
dataset = load_dataset("yelp_polarity", split="train") # https://huggingface.co/datasets/yelp_polarity

# take a small sample for dev purposes
dataset_sample = dataset.shuffle(seed=seed).select(range(100))

# user provided data description
DESCRIPTION = """
This is a dataset for binary sentiment classification.
It contains highly polar yelp reviews.
Negative polarity is class 0, and positive class 1.
"""

LABEL_SET = [0, 1] 

In [ ]:
prompt = [gemini_prompt_template.format(description= DESCRIPTION,
                                        datapoint=x,
                                        labels=LABEL_SET) for x in dataset_sample["text"][:20]]
print(len(prompt))

In [ ]:
ann = Annotate()

VALID_MODELS = ["gemini", "claude"]

In [ ]:
d = {}
for m in VALID_MODELS:
    d[m] = await ann.classification(prompt, model=m)

In [ ]:
import json
with open("./data/output/20_sample.json", "w") as json_file:
    json.dump(d, json_file, indent=4)

In [ ]:
# all_results = [d["gemini"], d["claude"]]
y_labels = ["gemini", "claude"]
all_results = [[1, 0, 0, 1, 1, 1, 1, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0],
               [1, 0, 0, 1, 1, 1, 1, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0]]

## evaluate

In [ ]:
from utils import Evaluate

eval = Evaluate()

In [ ]:
eval.classification(all_results, strategy="majority", visualize=True, y_labels=y_labels)

# Dev

In [ ]:
import scipy as sp
import numpy as np

In [ ]:
y_labels = ["gemini", "claude", "fake"]
all_results = [[1, 0, 0, 1, 1, 1, 1, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0],
               [1, 0, 0, 1, 1, 1, 1, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0],
               [0, 0, 1, 1, 0, 0, 1, 1, 1, 0, 0, 0, 0, 1, 1, 1, 0, 1, 1, 0]]


# task, labeler, label
result = [(j, i, sublist[i]) 
          for j, sublist in enumerate(all_results) 
          for i in range(len(sublist))]

In [ ]:
import argparse
import logging
import numpy as np
import scipy as sp
import scipy.stats
import scipy.optimize

THRESHOLD = 1e-5

logger = None


class Dataset(object):
    def __init__(self, labels=None, numLabels=-1, numLabelers=-1, numTasks=-1, numClasses=-1,
                 priorAlpha=None, priorBeta=None, priorZ=None,
                 alpha=None, beta=None, probZ=None):
        self.labels = labels
        self.numLabels = numLabels
        self.numLabelers = numLabelers
        self.numTasks = numTasks
        self.numClasses = numClasses
        self.priorAlpha = priorAlpha
        self.priorBeta = priorBeta
        self.priorZ = priorZ
        self.alpha = alpha
        self.beta = beta
        self.probZ = probZ


def init_logger():
    global logger
    logger = logging.getLogger('GLAD')
    logger.setLevel(logging.DEBUG)
    log_fmt = '%(asctime)s/%(name)s[%(levelname)s]: %(message)s'
    logging.basicConfig(format=log_fmt)


def sigmoid(x):
    return 1.0 / (1.0 + np.exp(-x))


def logsigmoid(x):
    return - np.log(1 + np.exp(-x))


def load_data(filename):
    data = Dataset()
    with open(filename) as f:
        header = f.readline().split()
        data.numLabels = int(header[0])
        data.numLabelers = int(header[1])
        data.numTasks = int(header[2])
        data.numClasses = int(header[3])
        data.priorZ = np.array([float(x) for x in header[4:]])
        assert len(data.priorZ) == data.numClasses, 'Incorrect input header'
        assert data.priorZ.sum() == 1, 'Incorrect priorZ given'

        data.labels = np.zeros((data.numTasks, data.numLabelers))
        for line in f:
            task, labeler, label = map(int, line.split())
            data.labels[task][labeler] = label + 1

    data.priorAlpha = np.ones(data.numLabelers)
    data.priorBeta = np.ones(data.numTasks)
    data.probZ = np.empty((data.numTasks, data.numClasses))
    data.beta = np.empty(data.numTasks)
    data.alpha = np.empty(data.numLabelers)

    return data


def EM(data):
    data.alpha = data.priorAlpha.copy()
    data.beta = data.priorBeta.copy()
    data.probZ[:] = data.priorZ[:]

    print(data.probZ[:])

    EStep(data)
    lastQ = computeQ(data)
    MStep(data)
    Q = computeQ(data)
    counter = 1
    while abs((Q - lastQ) / lastQ) > THRESHOLD:
        if verbose:
            logger.info('EM: iter={}'.format(counter))
        lastQ = Q
        EStep(data)
        MStep(data)
        Q = computeQ(data)
        counter += 1

def calcLogProbL(item, *args):
    data = args[-1]
    print(data.alpha, data.labels)

    j = int(item[0])
    delta = args[0][j]
    noResp = args[1][j]
    oneMinusDelta = (~delta) & (~noResp)

    exponents = item[1:]

    correct = logsigmoid(exponents[delta]).sum()
    wrong = (logsigmoid(-exponents[oneMinusDelta]) - np.log(float(data.numClasses - 1))).sum()

    return correct + wrong

def EStep(data):
    data.probZ = np.tile(np.log(data.priorZ), data.numTasks).reshape(data.numTasks, data.numClasses)

    ab = np.dot(np.array([np.exp(data.beta)]).T, np.array([data.alpha]))
    ab = np.c_[np.arange(data.numTasks), ab]
    for k in range(data.numClasses):
        data.probZ[:, k] = np.apply_along_axis(calcLogProbL, 1, ab,
                                               (data.labels == k + 1),
                                               (data.labels == 0),
                                               data)  # Pass data as an additional argument

    data.probZ = np.exp(data.probZ)
    s = data.probZ.sum(axis=1)
    data.probZ = (data.probZ.T / s).T
    assert not np.any(np.isnan(data.probZ)), 'Invalid Value [EStep]'
    assert not np.any(np.isinf(data.probZ)), 'Invalid Value [EStep]'



def df(x, *args):
    data = args[0]
    d = Dataset(labels=data.labels, numLabels=data.numLabels, numLabelers=data.numLabelers,
                numTasks=data.numTasks, numClasses=data.numClasses,
                priorAlpha=data.priorAlpha, priorBeta=data.priorBeta,
                priorZ=data.priorZ, probZ=data.probZ)
    unpackX(x, d)
    dQdAlpha, dQdBeta = gradientQ(d)
    return np.r_[-dQdAlpha, -dQdBeta]


def f(x, *args):
    u"""Return the value of the objective function
    """
    data = args[0]
    d = Dataset(labels=data.labels, numLabels=data.numLabels, numLabelers=data.numLabelers,
                numTasks=data.numTasks, numClasses=data.numClasses,
                priorAlpha=data.priorAlpha, priorBeta=data.priorBeta,
                priorZ=data.priorZ, probZ=data.probZ)
    unpackX(x, d)
    return - computeQ(d)

def MStep(data):
    initial_params = packX(data)
    params = sp.optimize.minimize(fun=f, x0=initial_params, args=(data,), method='CG',
                                  jac=df, tol=0.01,
                                  options={'maxiter': 25, 'disp': verbose})
    unpackX(params.x, data)


def computeQ(data):
    Q = 0
    Q += (data.probZ * np.log(data.priorZ)).sum()

    ab = np.dot(np.array([np.exp(data.beta)]).T, np.array([data.alpha]))

    logSigma = logsigmoid(ab)
    idxna = np.isnan(logSigma)
    if np.any(idxna):
        logger.warning('an invalid value was assigned to np.log [computeQ]')
        logSigma[idxna] = ab[idxna]

    logOneMinusSigma = logsigmoid(-ab) - np.log(float(data.numClasses - 1))
    idxna = np.isnan(logOneMinusSigma)
    if np.any(idxna):
        logger.warning('an invalid value was assigned to np.log [computeQ]')
        logOneMinusSigma[idxna] = -ab[idxna]

    for k in range(data.numClasses):
        delta = (data.labels == k + 1)
        Q += (data.probZ[:, k] * logSigma.T).T[delta].sum()
        oneMinusDelta = (data.labels != k + 1) & (data.labels != 0)
        Q += (data.probZ[:, k] * logOneMinusSigma.T).T[oneMinusDelta].sum()

    Q += np.log(sp.stats.norm.pdf(data.alpha - data.priorAlpha)).sum()
    Q += np.log(sp.stats.norm.pdf(data.beta - data.priorBeta)).sum()

    if np.isnan(Q):
        return -np.inf
    return Q


def gradientQ(data):
    dQdAlpha = - (data.alpha - data.priorAlpha)
    dQdBeta = - (data.beta - data.priorBeta)

    ab = np.dot(np.array([np.exp(data.beta)]).T, np.array([data.alpha]))
    sigma = sigmoid(ab)
    sigma[np.isnan(sigma)] = 0

    labelersIdx = np.arange(data.numLabelers).reshape((1, data.numLabelers))
    sigma = np.r_[labelersIdx, sigma]
    sigma = np.c_[np.arange(-1, data.numTasks), sigma]

    for k in range(data.numClasses):
        dQdAlpha += np.apply_along_axis(dAlpha, 0, sigma[:, 1:],
                                         (data.labels == k + 1),
                                         (data.labels == 0),
                                         data.probZ[:, k],
                                         data)

        dQdBeta += np.apply_along_axis(dBeta, 1, sigma[1:],
                                        (data.labels == k + 1),
                                        (data.labels == 0),
                                        data.probZ[:, k],
                                        data) * np.exp(data.beta)

    return dQdAlpha, dQdBeta


def dAlpha(item, *args):
    i = int(item[0])
    sigma_ab = item[1:]

    delta = args[0][:, i]
    noResp = args[1][:, i]
    oneMinusDelta = (~delta) & (~noResp)

    probZ = args[2]

    data = args[3] 

    correct = probZ[delta] * np.exp(data.beta[delta]) * (1 - sigma_ab[delta])
    wrong = probZ[oneMinusDelta] * np.exp(data.beta[oneMinusDelta]) * (-sigma_ab[oneMinusDelta])

    return correct.sum() + wrong.sum()


def dBeta(item, *args):
    j = int(item[0])
    sigma_ab = item[1:]

    delta = args[0][j]
    noResp = args[1][j]
    oneMinusDelta = (~delta) & (~noResp)

    probZ = args[2][j]
    data = args[3] 

    correct = probZ * data.alpha[delta] * (1 - sigma_ab[delta])
    wrong = probZ * data.alpha[oneMinusDelta] * (-sigma_ab[oneMinusDelta])

    return correct.sum() + wrong.sum()


def packX(data):
    return np.r_[data.alpha.copy(), data.beta.copy()]


def unpackX(x, data):
    data.alpha = x[:data.numLabelers].copy()
    data.beta = x[data.numLabelers:].copy()





def output(data):
    alpha = np.c_[np.arange(data.numLabelers), data.alpha]
    np.savetxt('data/alpha.csv', alpha, fmt=['%d', '%.5f'], delimiter=',', header='id,alpha')
    beta = np.c_[np.arange(data.numTasks), np.exp(data.beta)]
    np.savetxt('data/beta.csv', beta, fmt=['%d', '%.5f'], delimiter=',', header='id,beta')
    probZ = np.c_[np.arange(data.numTasks), data.probZ]
    np.savetxt(fname='data/probZ.csv',
               X=probZ,
               fmt=['%d'] + (['%.5f'] * data.numClasses),
               delimiter=',',
               header='id,' + ','.join(['z' + str(k) for k in range(data.numClasses)]))
    label = np.c_[np.arange(data.numTasks), np.argmax(data.probZ, axis=1)]
    np.savetxt('data/label_glad.csv', label, fmt=['%d', '%d'], delimiter=',', header='id,label')


def main():
    global debug, verbose
    init_logger()

    debug = True
    verbose = True

    data = load_data("./data/data.txt")

    EM(data)
    output(data)
    return



In [ ]:
main()

In [9]:
import argparse
import logging
import numpy as np
import scipy as sp
import scipy.stats
import scipy.optimize

THRESHOLD = 1e-5

logger = None


class Dataset(object):
    def __init__(self, labels=None, numLabels=-1, numLabelers=-1, numTasks=-1, numClasses=-1,
                 priorAlpha=None, priorBeta=None, priorZ=None,
                 alpha=None, beta=None, probZ=None):
        self.labels = labels
        self.numLabels = numLabels
        self.numLabelers = numLabelers
        self.numTasks = numTasks
        self.numClasses = numClasses
        self.priorAlpha = priorAlpha
        self.priorBeta = priorBeta
        self.priorZ = priorZ
        self.alpha = alpha
        self.beta = beta
        self.probZ = probZ


def init_logger():
    global logger
    logger = logging.getLogger('GLAD')
    logger.setLevel(logging.DEBUG)
    log_fmt = '%(asctime)s/%(name)s[%(levelname)s]: %(message)s'
    logging.basicConfig(format=log_fmt)


def sigmoid(x):
    return 1.0 / (1.0 + np.exp(-x))

def logsigmoid(x):
    return - np.logaddexp(0, -x) 


def load_data(filename):
    data = Dataset()
    with open(filename) as f:
        header = f.readline().split()
        data.numLabels, data.numLabelers, data.numTasks, data.numClasses = map(int, header[:4])
        data.priorZ = np.array(list(map(float, header[4:])))

        assert len(data.priorZ) == data.numClasses, 'Incorrect input header'
        assert np.isclose(data.priorZ.sum(), 1), 'Incorrect priorZ given' 

        # More efficient way to read and populate data.labels
        rows, cols, vals = [], [], []
        for line in f:
            task, labeler, label = map(int, line.split())
            rows.append(task)
            cols.append(labeler)
            vals.append(label + 1)

        data.labels = sp.sparse.coo_matrix((vals, (rows, cols)), 
                                          shape=(data.numTasks, data.numLabelers)).toarray()


    data.priorAlpha = np.ones(data.numLabelers)
    data.priorBeta = np.ones(data.numTasks)
    data.probZ = np.empty((data.numTasks, data.numClasses))
    data.beta = np.empty(data.numTasks)
    data.alpha = np.empty(data.numLabelers)

    return data


def EM(data):
    data.alpha = data.priorAlpha.copy()
    data.beta = data.priorBeta.copy()
    data.probZ[:] = data.priorZ[:]

    print(data.probZ[:])

    EStep(data)
    lastQ = computeQ(data)
    MStep(data)
    Q = computeQ(data)
    counter = 1
    while abs((Q - lastQ) / lastQ) > THRESHOLD:
        if verbose:
            logger.info('EM: iter={}'.format(counter))
        lastQ = Q
        EStep(data)
        MStep(data)
        Q = computeQ(data)
        counter += 1

def calcLogProbL(item, *args):
    data = args[-1]
    print(data.alpha, data.labels)

    j = int(item[0])
    delta = args[0][j]
    noResp = args[1][j]
    oneMinusDelta = (~delta) & (~noResp)

    exponents = item[1:]

    correct = logsigmoid(exponents[delta]).sum()
    wrong = (logsigmoid(-exponents[oneMinusDelta]) - np.log(float(data.numClasses - 1))).sum()

    return correct + wrong

def EStep(data):
    data.probZ = np.tile(np.log(data.priorZ), data.numTasks).reshape(data.numTasks, data.numClasses)

    ab = np.dot(np.array([np.exp(data.beta)]).T, np.array([data.alpha]))
    ab = np.c_[np.arange(data.numTasks), ab]
    for k in range(data.numClasses):
        data.probZ[:, k] = np.apply_along_axis(calcLogProbL, 1, ab,
                                               (data.labels == k + 1),
                                               (data.labels == 0),
                                               data)  # Pass data as an additional argument

    data.probZ = np.exp(data.probZ)
    s = data.probZ.sum(axis=1)
    data.probZ = (data.probZ.T / s).T
    assert not np.any(np.isnan(data.probZ)), 'Invalid Value [EStep]'
    assert not np.any(np.isinf(data.probZ)), 'Invalid Value [EStep]'



def df(x, *args):
    data = args[0]
    d = Dataset(labels=data.labels, numLabels=data.numLabels, numLabelers=data.numLabelers,
                numTasks=data.numTasks, numClasses=data.numClasses,
                priorAlpha=data.priorAlpha, priorBeta=data.priorBeta,
                priorZ=data.priorZ, probZ=data.probZ)
    unpackX(x, d)
    dQdAlpha, dQdBeta = gradientQ(d)
    return np.r_[-dQdAlpha, -dQdBeta]


def f(x, *args):
    u"""Return the value of the objective function
    """
    data = args[0]
    d = Dataset(labels=data.labels, numLabels=data.numLabels, numLabelers=data.numLabelers,
                numTasks=data.numTasks, numClasses=data.numClasses,
                priorAlpha=data.priorAlpha, priorBeta=data.priorBeta,
                priorZ=data.priorZ, probZ=data.probZ)
    unpackX(x, d)
    return - computeQ(d)

def MStep(data):
    initial_params = packX(data)
    params = sp.optimize.minimize(fun=f, x0=initial_params, args=(data,), method='CG',
                                  jac=df, tol=0.01,
                                  options={'maxiter': 25, 'disp': verbose})
    unpackX(params.x, data)


def computeQ(data):
    Q = 0
    Q += (data.probZ * np.log(data.priorZ)).sum()

    ab = np.dot(np.array([np.exp(data.beta)]).T, np.array([data.alpha]))

    logSigma = logsigmoid(ab)
    idxna = np.isnan(logSigma)
    if np.any(idxna):
        logger.warning('an invalid value was assigned to np.log [computeQ]')
        logSigma[idxna] = ab[idxna]

    logOneMinusSigma = logsigmoid(-ab) - np.log(float(data.numClasses - 1))
    idxna = np.isnan(logOneMinusSigma)
    if np.any(idxna):
        logger.warning('an invalid value was assigned to np.log [computeQ]')
        logOneMinusSigma[idxna] = -ab[idxna]

    for k in range(data.numClasses):
        delta = (data.labels == k + 1)
        Q += (data.probZ[:, k] * logSigma.T).T[delta].sum()
        oneMinusDelta = (data.labels != k + 1) & (data.labels != 0)
        Q += (data.probZ[:, k] * logOneMinusSigma.T).T[oneMinusDelta].sum()

    Q += np.log(sp.stats.norm.pdf(data.alpha - data.priorAlpha)).sum()
    Q += np.log(sp.stats.norm.pdf(data.beta - data.priorBeta)).sum()

    if np.isnan(Q):
        return -np.inf
    return Q


def gradientQ(data):
    dQdAlpha = - (data.alpha - data.priorAlpha)
    dQdBeta = - (data.beta - data.priorBeta)

    ab = np.exp(data.beta)[:, np.newaxis] * data.alpha
    sigma = sigmoid(ab)
    sigma[np.isnan(sigma)] = 0

    for k in range(data.numClasses):
        delta = (data.labels == k + 1)
        oneMinusDelta = (data.labels != k + 1) & (data.labels != 0)

        dQdAlpha += (data.probZ[:, k][:, np.newaxis] * np.exp(data.beta)[:, np.newaxis] * (delta - sigma)).sum(axis=0)
        dQdBeta += (data.probZ[:, k][:, np.newaxis] * data.alpha * (delta - sigma)).sum(axis=1)

    return dQdAlpha, dQdBeta


def dAlpha(item, *args):
    i = int(item[0])
    sigma_ab = item[1:]

    delta = args[0][:, i]
    noResp = args[1][:, i]
    oneMinusDelta = (~delta) & (~noResp)

    probZ = args[2]

    data = args[3] 

    correct = probZ[delta] * np.exp(data.beta[delta]) * (1 - sigma_ab[delta])
    wrong = probZ[oneMinusDelta] * np.exp(data.beta[oneMinusDelta]) * (-sigma_ab[oneMinusDelta])

    return correct.sum() + wrong.sum()


def dBeta(item, *args):
    j = int(item[0])
    sigma_ab = item[1:]

    delta = args[0][j]
    noResp = args[1][j]
    oneMinusDelta = (~delta) & (~noResp)

    probZ = args[2][j]
    data = args[3] 

    correct = probZ * data.alpha[delta] * (1 - sigma_ab[delta])
    wrong = probZ * data.alpha[oneMinusDelta] * (-sigma_ab[oneMinusDelta])

    return correct.sum() + wrong.sum()


def packX(data):
    return np.r_[data.alpha.copy(), data.beta.copy()]


def unpackX(x, data):
    data.alpha = x[:data.numLabelers].copy()
    data.beta = x[data.numLabelers:].copy()





def output(data):
    alpha = np.c_[np.arange(data.numLabelers), data.alpha]
    np.savetxt('data/alpha.csv', alpha, fmt=['%d', '%.5f'], delimiter=',', header='id,alpha')
    beta = np.c_[np.arange(data.numTasks), np.exp(data.beta)]
    np.savetxt('data/beta.csv', beta, fmt=['%d', '%.5f'], delimiter=',', header='id,beta')
    probZ = np.c_[np.arange(data.numTasks), data.probZ]
    np.savetxt(fname='data/probZ.csv',
               X=probZ,
               fmt=['%d'] + (['%.5f'] * data.numClasses),
               delimiter=',',
               header='id,' + ','.join(['z' + str(k) for k in range(data.numClasses)]))
    label = np.c_[np.arange(data.numTasks), np.argmax(data.probZ, axis=1)]
    np.savetxt('data/label_glad.csv', label, fmt=['%d', '%d'], delimiter=',', header='id,label')


def main():
    global debug, verbose
    init_logger()

    debug = True
    verbose = True

    data = load_data("./data/data.txt")

    EM(data)
    output(data)
    return



In [10]:
main()

[[0.5 0.5]
 [0.5 0.5]
 [0.5 0.5]
 ...
 [0.5 0.5]
 [0.5 0.5]
 [0.5 0.5]]
[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[1. 1. 1. 1. 1. 1.

/usr/local/google/home/amirimani/Desktop/projects/LLMTest_NeedleInAHaystack/.venv/lib/python3.11/site-packages/scipy/optimize/_minimize.py:706: OptimizeWarning: Desired error not necessarily achieved due to precision loss.
  res = _minimize_cg(fun, x0, args, jac, callback, **options)
2024-05-10 20:59:17,926/GLAD[INFO]: EM: iter=1


         Current function value: 11068.776254
         Iterations: 10
         Function evaluations: 63
         Gradient evaluations: 51
[0.33345371 0.3207556  0.39079854 0.3628253  0.37659872 0.35004169
 0.40074052 0.33531216 0.31432087 0.33278477 0.39006528 0.35239258
 0.3895181  0.37338341 0.34953519 0.39974443 1.37808129 1.50999423
 1.55946349 1.46599082] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[0.33345371 0.3207556  0.39079854 0.3628253  0.37659872 0.35004169
 0.40074052 0.33531216 0.31432087 0.33278477 0.39006528 0.35239258
 0.3895181  0.37338341 0.34953519 0.39974443 1.37808129 1.50999423
 1.55946349 1.46599082] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[0.33345371 0.3207556  0.39079854 0.3628253  0.37659872 0.35004169
 0.40074052 0.33531216 0.31432087 0.33278477 0.39006528 0.35239258
 0.3895181  0.37338341 0.34953519 0.39

/usr/local/google/home/amirimani/Desktop/projects/LLMTest_NeedleInAHaystack/.venv/lib/python3.11/site-packages/scipy/optimize/_minimize.py:706: OptimizeWarning: Desired error not necessarily achieved due to precision loss.
  res = _minimize_cg(fun, x0, args, jac, callback, **options)
2024-05-10 20:59:19,661/GLAD[INFO]: EM: iter=2


         Current function value: 10959.215146
         Iterations: 16
         Function evaluations: 88
         Gradient evaluations: 77
[0.34725424 0.32395091 0.41196451 0.37863365 0.40075937 0.36858295
 0.41610869 0.35090768 0.33727371 0.33956791 0.4098011  0.36570255
 0.41077217 0.39734819 0.36242067 0.40768856 1.82544745 1.91169988
 1.92596248 1.79220965] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[0.34725424 0.32395091 0.41196451 0.37863365 0.40075937 0.36858295
 0.41610869 0.35090768 0.33727371 0.33956791 0.4098011  0.36570255
 0.41077217 0.39734819 0.36242067 0.40768856 1.82544745 1.91169988
 1.92596248 1.79220965] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[0.34725424 0.32395091 0.41196451 0.37863365 0.40075937 0.36858295
 0.41610869 0.35090768 0.33727371 0.33956791 0.4098011  0.36570255
 0.41077217 0.39734819 0.36242067 0.40

...

/usr/local/google/home/amirimani/Desktop/projects/LLMTest_NeedleInAHaystack/.venv/lib/python3.11/site-packages/scipy/optimize/_minimize.py:706: OptimizeWarning: Desired error not necessarily achieved due to precision loss.
  res = _minimize_cg(fun, x0, args, jac, callback, **options)
2024-05-10 20:59:23,005/GLAD[INFO]: EM: iter=4


         Current function value: 10919.528367
         Iterations: 3
         Function evaluations: 47
         Gradient evaluations: 35
[0.35621113 0.35265726 0.41748515 0.38957623 0.40510832 0.38118397
 0.43406388 0.36026794 0.3536374  0.35380581 0.4205285  0.37823655
 0.42128109 0.39825498 0.36668313 0.424326   1.88441274 2.45080979
 2.41314912 2.1234446 ] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[0.35621113 0.35265726 0.41748515 0.38957623 0.40510832 0.38118397
 0.43406388 0.36026794 0.3536374  0.35380581 0.4205285  0.37823655
 0.42128109 0.39825498 0.36668313 0.424326   1.88441274 2.45080979
 2.41314912 2.1234446 ] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[0.35621113 0.35265726 0.41748515 0.38957623 0.40510832 0.38118397
 0.43406388 0.36026794 0.3536374  0.35380581 0.4205285  0.37823655
 0.42128109 0.39825498 0.36668313 0.424

/usr/local/google/home/amirimani/Desktop/projects/LLMTest_NeedleInAHaystack/.venv/lib/python3.11/site-packages/scipy/optimize/_minimize.py:706: OptimizeWarning: Desired error not necessarily achieved due to precision loss.
  res = _minimize_cg(fun, x0, args, jac, callback, **options)
2024-05-10 20:59:24,605/GLAD[INFO]: EM: iter=5


         Current function value: 10917.885755
         Iterations: 1
         Function evaluations: 47
         Gradient evaluations: 36
[0.35780052 0.34488296 0.41410281 0.38989249 0.40489107 0.38164393
 0.43456027 0.36251426 0.34784779 0.3600222  0.41865042 0.37868204
 0.41883118 0.39824276 0.3710633  0.42517778 1.88358609 2.45052129
 2.41275452 2.12306306] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[0.35780052 0.34488296 0.41410281 0.38989249 0.40489107 0.38164393
 0.43456027 0.36251426 0.34784779 0.3600222  0.41865042 0.37868204
 0.41883118 0.39824276 0.3710633  0.42517778 1.88358609 2.45052129
 2.41275452 2.12306306] [[2 2 1 ... 2 2 2]
 [2 2 2 ... 2 2 2]
 [1 2 1 ... 1 1 1]
 ...
 [1 1 1 ... 2 2 2]
 [1 1 2 ... 2 2 2]
 [2 2 1 ... 1 1 1]]
[0.35780052 0.34488296 0.41410281 0.38989249 0.40489107 0.38164393
 0.43456027 0.36251426 0.34784779 0.3600222  0.41865042 0.37868204
 0.41883118 0.39824276 0.3710633  0.425

/usr/local/google/home/amirimani/Desktop/projects/LLMTest_NeedleInAHaystack/.venv/lib/python3.11/site-packages/scipy/optimize/_minimize.py:706: OptimizeWarning: Desired error not necessarily achieved due to precision loss.
  res = _minimize_cg(fun, x0, args, jac, callback, **options)
